In [1]:
import numpy as np


In [4]:
from mpl_toolkits.mplot3d import Axes3D
#from matplotlib.colors import LinearSegmentedColormap
import matplotlib.pyplot as plt

In [5]:
import plotly
import plotly.plotly as py
import plotly.graph_objs as go
from plotly import tools
plotly.offline.init_notebook_mode(connected=True)

import pandas as pd

## <center>**Transition to Riemann invariants**</center>
<center>**1D:**</center>


Равновесное состояние характеризуется нулевой скоростью течения газов, плотностью $\rho _0$, давлением $P(\rho_0)$. Неизвестными функциями являются давление $p(x,t)$ и скорость $u(x,t)$, как малые величины относительно равновестных значений.
Если ввести обозначение $K_0 = \rho_0 P'(\rho_0)$, то динамические процессы, происходящие в среде, могут быть описаны линейной системой дифференциальных уравнений:
$$\begin{bmatrix}
p\\
u
\end{bmatrix}_t+ 
\begin{bmatrix}
0 & K_0\\
\dfrac{1}{\rho_0} & 0
\end{bmatrix}
\begin{bmatrix}
p\\
u
\end{bmatrix}_x = 0$$

<center>**2D:**</center>
$$\begin{bmatrix}
p\\
u\\
v
\end{bmatrix}_t+ 
\begin{bmatrix}
0 & K_0 & 0\\
\dfrac{1}{\rho_0} & 0& 0\\
0 & 0 & 0 
\end{bmatrix}
\begin{bmatrix}
p\\
u\\
v
\end{bmatrix}_x +
\begin{bmatrix}
0 & 0 & K_0 \\
0 & 0 & 0 \\
\dfrac{1}{\rho_0} & 0 & 0\\
\end{bmatrix}
\begin{bmatrix}
p\\
u\\
v
\end{bmatrix}_y
= 0
$$

Исходная система уравнений:

$\textbf{q}_t+\textbf{A}\textbf{q}_x+\textbf{B}\textbf{q}_y = \textbf{0}$

,где $\textbf{q} = \begin{bmatrix}
p\\
u\\
v
\end{bmatrix},\;\; \textbf{A} = \begin{bmatrix}
0 & K_0 & 0\\
\dfrac{1}{\rho_0} & 0& 0\\
0 & 0 & 0 
\end{bmatrix},\;\; \textbf{B} = \begin{bmatrix}
0 & 0 & K_0 \\
0 & 0 & 0 \\
\dfrac{1}{\rho_0} & 0& 0
\end{bmatrix}, ~~\rho ~-~ плотность~среды,~K - модуль~упругости$

Все параметры среды постоянны во всей области интегрирования.

В область интегрирования вводится равномерная прямоугольная сетка с
постоянными шагами $h_x$
и
$h_y$
по каждой оси. При решении многомерных задач
математической физики часто строятся локально-одномерные разностные схемы (метод
покоординатного расщепления). В литературе известно большое количество разных
методов расщепления по пространственным переменным с разными свойствами. Для
численного интегрирования уравнений акустики в двумерной области будем применять
следующий метод расщепления по пространственным координатам. Введем два
произвольных действительных параметра следующим образом

$(\alpha_1+\alpha_2)\textbf{q}_t+\frac{\alpha_1}{\alpha_1}\textbf{Aq}_x+\frac{\alpha_2}{\alpha_2}\textbf{Bq}_y$

$0<\alpha_{1,2}<1,~~ \alpha_1+\alpha_2 = 1,~~\alpha_1h_x=\alpha_2h_y$

В нашем случаее $h_x = h_y \Rightarrow ~\alpha_{1,2} = \frac{1}{2}$

Разобъём формальную задачу на две независимые задачи:

$\textbf{q}_{1t} + \frac{1}{2}\textbf{Aq}_{1x} = 0, ~~\textbf{q}_{2t} + \frac{1}{2}\textbf{Bq}_{2y} = 0$

Каждая задача зависит только от одной пространственной переменной. Эти задачи
можно решать одновременно, может быть, на разных исполнителях. Затем
восстанавливается значение

$\textbf{q} = \frac{\mathbf{q_1+q_2}}{2}$

Непосредственно проверяется, что у матрицы $A$ имеется полная система из
собственных векторов. Это означает, что можно составить матрицу $L$ левых и матрицу $R$
правых собственных векторов.
Приведем одномерную систему к инвариантам Римана, умножив уравнения слева
на матрицу левых собственных векторов:

$\begin{equation*}
 \begin{cases}
   \textbf{w}_t+\mathbf{\Lambda} \mathbf{w_x} = 0
   \\
   \textbf{w = L q}
 \end{cases}
\end{equation*}$

$\mathbf{\Lambda} = \frac{1}{\alpha_1}\begin{bmatrix}
-c & 0 & 0\\
0 & 0& 0\\
0 & 0 & c
    \end{bmatrix},~c=\sqrt{\frac{K}{\rho}}$ - скорость звука в среде, $\mathbf{w} = (w_1,w_2,w_3)^{\top}$ - вектор инвариантов Римана.
    
Получаем запись исходной системы уравнений в инвариантах Римана. Поскольку
матрица $\mathbf{\Lambda}$ в данной системе диагональная, то полученная система уравнений состоит из
трех независимых уравнений переноса. Их можно решать независимо, используя любую
из конечно-разностных схем.

После того, как все уравнения переноса решены, нам необходимо найти решение в
естественных переменных, для этого умножим вектор из инвариантов Римана на матрицу
$\mathbf{R}$, учитывая что
$\mathbf{R} = \mathbf{L}^{-1} : ~\mathbf{q}= \mathbf{Rw}$


Опишем алгоритм для программной реализации, основываясь на описанных методах:

1. Решаем одномерную гиперболическую задачу, зависящую только от переменной $x$.

    Матрицы правых и левых собственных векторов будут иметь вид
    
    $\mathbf{R_x} = \begin{bmatrix}
-Z & 0 & Z\\
1 & 0 & 1\\
0 & 1 & 0
    \end{bmatrix},~\mathbf{L_x} = \dfrac{1}{2}\begin{bmatrix}
-\frac{1}{Z} & 1 & 0\\
0 & 0 & 2\\
\frac{1}{Z} & 1 & 0
    \end{bmatrix},~~Z = \sqrt{K\rho}$



2. Переходим к инвариантам Римана и решаем независимо набор линейных уравнений переноса.


3. На основе решения в инвариантах Римана, полученного на шаге 2 алгоритма, получаемрешения на первом шаге расщепления, $\mathbf{q_A^{n+1}} = R_x\mathbf{w^{n+1}}$



4. Повторяем шаги 1-3, решаем одномерную гиперболическую задачу, зависящую только от переменной $y$. Матрицы левых и правых векторов:
    $\mathbf{R_y} = \begin{bmatrix}
-Z & 0 & Z\\
0 & 1 & 0\\
1 & 0 & 1
    \end{bmatrix},~\mathbf{L_y} = \dfrac{1}{2}\begin{bmatrix}
-\frac{1}{Z} & 0 & 1\\
           0 & 2 & 0\\
\frac{1}{Z}  & 0 & 1
    \end{bmatrix},~~Z = \sqrt{K\rho},~~\mathbf{q_B^{n+1}} = \mathbf{R_yw^{n+1}}$


5. На основе полученных решений $\mathbf{q_A^{n+1}},~\mathbf{q_B^{n+1}}$
   востанавливаем исходное решение $\mathbf{q^{n+1}}=\frac{1}{2}(\mathbf{q_A^{n+1}+q_B^{n+1}})$



6. Переходим к следующему шагу расчёта по времени


In [6]:
def RiemannTransform_node(q, direct, Z):
    w = [0]*3
    ind = []
    if direct == 'x':
        ind = [0,1,2]
    elif direct == 'y':
        ind = [0,2,1]
    #else:
        #return 'unexpected value of direct'
    
    w[0] = 1/2*(-q[ind[0]]/Z + q[ind[1]])
    w[1] = q[ind[2]]
    w[2] = 1/2*(q[ind[0]]/Z + q[ind[1]])
    
    return w

In [7]:
def BackRiemannTransform_node(w, direct, Z):
    q = [0]*3
    ind = [0,1,2]
    if direct == 'x':
        ind = [0,1,2]
    elif direct == 'y':
        ind = [0,2,1]
    
    q[ind[0]] = -Z*w[0] + Z*w[2]
    q[ind[1]] = w[0] + w[2]
    q[ind[2]] = w[1]
    
    return q

In [8]:
def RiemannTransform_mat(q, size, direct, Z, way):  
    if (way != "back") and (way != "forward"):
        return 'unexpected value of way'
    
    w = np.zeros((3,size,size))
    for i in range(size):
        for j in range(size):
            q3 = [q[0][i][j], q[1][i][j], q[2][i][j]]
            if way == "forward":
                w[0][i][j], w[1][i][j], w[2][i][j] = RiemannTransform_node(q3, direct, Z)
            elif way == "back":
                w[0][i][j], w[1][i][j], w[2][i][j] = BackRiemannTransform_node(q3, direct, Z)
    return w

## <center>**Compact Scheme**</center>

Для уравнения переноса $$u_t+\lambda u_x = 0$$

дополнительно рассматривается дифференциальное следствие
$$\nu_t+\lambda \nu_x = 0$$

где $\nu(x,t)=u_x(x,t)$ - дополнительная искомая функция.

В качестве начального условия может быть записано выражение $\nu(x,0) = u_x(x,0)$.

$$u(x_m,t_n+\tau) = u(x_m - \lambda \tau, t_n)$$
$$u(x_m,t_n+\tau) = u(x_m - \lambda \tau, t_n)$$

Используя двухточечный по пространству шаблон, можем восстановить полином третьей степени, интерполирующий значения в узлах шаблона.

$$u^n(x)=F_3(x)=a_3x^3+b_3x^2+c_3x+d_3,$$
$$\nu^n(x) = F_3'(x) = 3a_3x^2+2b_3x+c_3.$$

Обозначая, $u^n_{m'} = u^n_{x_m - h\cdot sign(\lambda)}$, $\nu^n_{m'} = \nu^n_{x_m - h\cdot sign(\lambda)}$, получим коэффициенты полинома:

$$a_3 = \frac{\nu_m^n+\nu^n{m'}}{h^2}-2\frac{u^n_m-u^n_{m'}}{h^3},$$
$$b_3 = \frac{2\nu_m^n+\nu^n{m'}}{h}-3\frac{u^n_m-u^n_{m'}}{h^2},$$
$$c_3 = \nu_m^n,$$
$$d_3 = u_m^n.$$


In [9]:
def CompactScheme_3(w_1, w_2, dw_1, dw_2, c_0, tau, h):
    if (c_0 < 0): # to keep uniformity of formulas 
        h = -h

    a = (dw_1 + dw_2)/(h ** 2) - 2*(w_1 - w_2)/(h ** 3)
    b = (dw_2 + 2 * dw_1)/h - 3*(w_1 - w_2)/(h ** 2)
    c = dw_1
    d = w_1
    
    x = -c_0 * tau
    w_1_upd = a * x ** 3 + b * x ** 2 + c * x + d
    dw_1_upd = 3 * a * x ** 2 + 2 * b * x + c
    
    return w_1_upd, dw_1_upd

### Расчёт

In [10]:
def OneDirectionComp(w_mat, dw_mat, size, c, tau, h, direct):  #order = 3
    w_mat_upd = np.zeros((size,size))
    dw_mat_upd = np.zeros((size,size))
    k = 0 #what neighbor node to use
    if c < 0:
        k = 1
    elif c > 0:
        k = -1
    for i in range(size):
        for j in range(size):
            w_1 = w_mat[i][j]
            dw_1 = dw_mat[i][j]
            i_= i
            j_ = j
            if direct == 'x':
                i_ = i
                j_ = (j + k) % size
            elif direct == 'y':
                i_ = (i + k) % size
                j_ = j
                
            w_2 = w_mat[i_][j_]
            dw_2 = dw_mat[i_][j_]

            w_mat_upd[i][j], dw_mat_upd[i][j] = CompactScheme_3(w_1, w_2, dw_1, dw_2, c, tau, h)
                
    return w_mat_upd, dw_mat_upd

In [11]:
def RecomputeFull(start_layers, size, c, tau, h, n_iter, Z):
    iter_layers = [None] * (n_iter + 1)
    iter_layers[0] = start_layers.copy()
    for epoch in range(1, n_iter + 1):
        layers = iter_layers[epoch - 1].copy()
        q_1 = layers['q_1']
        dw_1_dx = layers['dw_1_dx']
        dw_1_dy = layers['dw_1_dy']
        q_2 = layers['q_2']
        dw_2 = layers['dw_2']
        q_3 = layers['q_3']
        dw_3 = layers['dw_3']
        
        q = np.array((q_1,q_2,q_3))
        w_x = RiemannTransform_mat(q, size, 'x', Z, "forward")
        w_y = RiemannTransform_mat(q, size, 'y', Z, "forward")
        
        w_1_y, layers['dw_1_dy'] = OneDirectionComp(w_y[0], dw_1_dy, size, -2*c, tau, h, 'y')
        w_3_y, layers['dw_3'] = OneDirectionComp(w_y[2], dw_3, size, 2*c, tau, h, 'y')
        w_2_y = w_y[1]
        w_y = np.array((w_1_y,w_2_y,w_3_y))
        q_y = RiemannTransform_mat(w_y, size, 'y', Z, "back")
        
        w_1_x, layers['dw_1_dx'] = OneDirectionComp(w_x[0], dw_1_dx, size, -2*c, tau, h, 'x')
        w_3_x, layers['dw_3'] = OneDirectionComp(w_x[2], dw_3, size, 2*c, tau, h, 'x')
        w_2_x = w_x[1]
        w_x = np.array((w_1_x,w_2_x,w_3_x))
        q_x = RiemannTransform_mat(w_x, size, 'x', Z, "back")
        
        q = (q_x + q_y)/2
        
        layers['q_1'], layers['q_2'], layers['q_3'] = q[0], q[1], q[2]
        iter_layers[epoch] = layers.copy()

    return iter_layers

## Initial conditions
Рассматриваются начальные условия двух типов: «плоская волна» и «радиальный взрыв».

«Плоская волна» — это распространяющаяся в заданном направлении $\mathbf k$ волна. Начальное условие
для возмущения, которое приводит к распространению плоской волны, не может быть
произвольным. Вектор начальных условий в области возмущения должен быть
пропорциональным собственному вектору матрицы
$\mathbf {A_k}$.

$\mathbf k = (k_x,k_y)^{\top},~\mathbf{A_k}= \mathbf{A}k_x+\mathbf{B}k_y = \begin{bmatrix}
0 & k_xK & k_yK\\
\dfrac{k_x}{\rho_0} & 0& 0\\
\dfrac{k_y}{\rho_0} & 0 & 0 
\end{bmatrix}$

C учётом нормировки $k_x^2+k_y^2 = 1$, найдём собственные числа матрицы: $\lambda = -c,0,c~(c=\sqrt{\frac{K}{\rho}})$.   

Собственные векторы же: $\mathbf h_{\mathbf{k},1} = \begin{bmatrix}
-Z\\
k_x\\
k_y 
\end{bmatrix},~\mathbf h_{\mathbf{k},2} = \begin{bmatrix}
0\\
k_y\\
k_x 
\end{bmatrix},~\mathbf h_{\mathbf{k},3} = \begin{bmatrix}
Z\\
k_x\\
k_y 
\end{bmatrix}$

В качестве коэффициента
пропорциональности может быть использована ограниченная функция одной переменной
(координата считается в направлении распространения волны), например, функция
Гаусса.

$$\large{g(x) = ae^{\frac{-(x-b)^2}{2c^2}}}$$

In [12]:
def make_square_grid(size, h):
    temp = (size - 1) * h / 2
    x = np.linspace(-temp, temp, size)
    y = np.linspace(-temp, temp, size)
    xgrid, ygrid = np.meshgrid(x, y)
    return xgrid, ygrid

In [13]:
def gauss_2d(a, bx, by, cx, cy, x, y):
    return a * np.exp(-(x-bx)**2 / (2 * cx**2)-(y-by)**2 / (2 * cy**2))

In [14]:
def norm_k(k):
    abs_k = np.sqrt(k['k_x']**2 + k['k_y']**2)
    k['k_x'], k['k_y'] = k['k_x'] / abs_k, k['k_y'] / abs_k
    return k

## Условие Куранта — Фридрихса — Леви
Необходимое условие Куранта устойчивости явного численного решения заключается в том, что отношение временного шага к пространственному не должен быть ограничен. 

$$\tau \leq \min \left({\frac  {h}{|\lambda |_{{max}}}}\right)$$

В нашем случае $|\lambda |_{{max}} = c = 1$, поэтому при $ \tau \leq h$, условие выполнено.

In [15]:
size = 100
c = 1
tau = 0.09
h = 0.2
Z = 0.1

layers = {}
layers_ = {}
keys = ['q_1', 'dw_1_dx', 'dw_1_dy', 'q_2', 'dw_2', 'q_3', 'dw_3']
for name in keys:
    layers[name] = np.zeros((size, size))

In [16]:
layers['dw_1_dx'],layers['dw_1_dy'],layers['dw_2'],layers['dw_3'] = np.zeros((size,size)),np.zeros((size,size)),np.zeros((size,size)),np.zeros((size,size))

In [17]:
def plot_one(q, range_ = [-1,1]):
    data = [
    go.Surface(
        z=q
    )
    ]
    layout = go.Layout(
        scene=dict(
            zaxis=dict(
                showbackground=True,
                range = range_
            )
        )
    )
    fig = go.Figure(data=data, layout = layout)
    plotly.offline.iplot(fig)

In [18]:
def animate_one(iter_layers, n_iter):
    frames = []
    for epoch in range(n_iter + 1):
        frames.append({'data': [go.Surface(z = iter_layers[epoch]['q_1'])]})
    figure = {
          'data': [go.Surface(z = iter_layers[0]['q_1'])],
          'layout': {'scene': {'zaxis': {'range': [-1, 1], 'autorange': False, 'showbackground' : True,}},
                     'updatemenus': [{'type': 'buttons',
                                      'buttons': [{'label': 'Play',
                                                   'method': 'animate',
                                                   'args': [
                                    None, 
                                    dict(frame=dict(duration=70, redraw=False),
                                         transition=dict(duration=0),
                                         fromcurrent=True,
                                         mode='immediate')
                                ]}]}]
                    },
          'frames': frames
         }

    plotly.offline.iplot(figure)

In [19]:
def plot_three(q1, q2, q3, range_ = [-1,1]):
    fig = tools.make_subplots(rows=1, cols=3,specs=[[{'is_3d': True} for i in range(3)]])
    q = [q1,q2,q3]
    graphs = []
    data = []
    for i in range(3):
        graphs.append(go.Surface(z=q[i]))
        scene=dict(
                zaxis=dict(
                showbackground=True
                ,range = range_
                #range = [-1,layers_['q_2'].max()*3]
                )
        )
        data.append(graphs[i])
        fig.append_trace(graphs[i], 1, i+1)
        fig['layout']['scene'+str(i+1)].update(scene)
    plotly.offline.iplot(fig)

In [20]:
#def animate_three(iter_layers):

## Radial explosion

In [21]:
Z = 1

In [22]:
def start_q_radial(size, h, r, R, a, b, c, Z):
    temp = (size - 1) * h
    x, y = make_square_grid(size, h)
    z = np.zeros((size,size))
    z2 = np.zeros((size,size))
    z3 = np.zeros((size,size))
    
    rad = np.sqrt(x**2 + y**2)
    z = np.exp(-(np.sqrt(x**2 + y**2) - (R - r)*temp/2)**2 / (2 * c**2))   
    z2 =  z * x / rad
    z3 =  z * y / rad

    return z * Z, z2, z3

In [23]:
layers['dw_1_dx'],layers['dw_1_dy'],layers['dw_2'],layers['dw_3'] = np.zeros((size,size)),np.zeros((size,size)),np.zeros((size,size)),np.zeros((size,size))
layers['q_1'],layers['q_2'],layers['q_3'] = start_q_radial(size, h = h, r = 0.05, R = 0.2, a = 1, b = 0, c = 1, Z = Z)

In [108]:
plot_three(layers['q_1'],layers['q_2'],layers['q_3'], [-2,2])

This is the format of your plot grid:
[ (1,1) scene1 ]  [ (1,2) scene2 ]  [ (1,3) scene3 ]



In [119]:
n_iter = 500

In [ ]:
iter_layers = RecomputeFull(layers, size, c = c, tau = tau, h = h, n_iter = n_iter, Z = Z)

In [ ]:
plot_three(iter_layers[n_iter]['q_1'],iter_layers[n_iter]['q_2'],iter_layers[n_iter]['q_3'], [-1,1])

In [ ]:
animate_one(iter_layers, n_iter)

## Flat wave

In [24]:
Z = 0.1

In [25]:
def start_q_plane(size, h, k, a, bx, by, cx, cy, Z):
    k = norm_k(k)
    x, y = make_square_grid(size, h)
    z = np.zeros((size,size))
    z = a * np.exp(-(x-bx)**2 / (2 * cx**2))
    
    
    return z * Z, z * k['k_x'], z * k['k_y']

In [26]:
k = {'k_x':1, 'k_y':0}

In [27]:
layers['dw_1_dx'],layers['dw_1_dy'],layers['dw_2'],layers['dw_3'] = np.zeros((size,size)),np.zeros((size,size)),np.zeros((size,size)),np.zeros((size,size))

In [39]:
layers['q_1'],layers['q_2'],layers['q_3'] = start_q_plane(size, h = h, k = k, a = 10.0, bx = 0, by = 0, cx = 0.3, cy = 0.3, Z = Z)

In [41]:
plot_three(layers['q_1'],layers['q_2'],layers['q_3'], [-1,1])

This is the format of your plot grid:
[ (1,1) scene1 ]  [ (1,2) scene2 ]  [ (1,3) scene3 ]



In [46]:
n_iter = 300

In [47]:
iter_layers = RecomputeFull(layers, size, c = c, tau = tau, h = h, n_iter = n_iter, Z = Z)

In [48]:
plot_three(iter_layers[n_iter]['q_1'],iter_layers[n_iter]['q_2'],iter_layers[n_iter]['q_3'], [-1,1])

This is the format of your plot grid:
[ (1,1) scene1 ]  [ (1,2) scene2 ]  [ (1,3) scene3 ]



In [ ]:
animate_one(iter_layers, n_iter)